In [2]:
#Import libraries
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report

In [5]:
#I resue the code from Abtin's notebook
def Entropy(prob_X):
    """
    This is the entropy function that computes
    entropy  of a  given  random  variables  X
    and with  their corresponding probabilities
    p_i based on the definition in:

    Shanon and Weaver, 1949

    -> Links to paper :
    --> http://math.harvard.edu/~ctm/home/text/others/shannon/entropy/entropy.pdf
    --> https://ieeexplore.ieee.org/document/6773024


              Entropy = Σ_i p_i * log2 (p_i)


    INPUT:
    -------
            prob_X (a list/array of variables):  

       it should contains all the  probabilities of
       the underlying random variable, each element
       expected to be a (0 <= float) and should
       add up to 1. (Else will be normalized)



    OUTPUT:
    -------
            Entropy (float): Entropy bits
    """
    import math
    _sum_ = 0

    _tot_ = 0
    # checks
    for prob in prob_X:
        assert prob >= 0, "Negative probability is not accepted!!!"
        _tot_ += prob

#     if _tot_!=1:
#         print("Inputs are not normalized added up to {}, will be normalized!!".format(_tot_))

    for prob in prob_X:
        if _tot_==0:
            continue

        prob = prob/_tot_
        if prob == 0:
            pass
        else:
            _sum_ += prob * math.log2(prob)

    return abs(_sum_)


def Boolean_Entropy(q):
    """
    Finds the entropy for a Boolean random variable.

    INPUT:
    ------
           q (float) : is expected to be between 0 and 1 (else AssertionError)

    OUTPUT:
    -------
            Entropy (float) : Entropy of a throwing a coin with chances
                              of P(H, T) = (q, 1 - q) in bits


    """
    assert q >= 0 and q <= 1, "q = {} is not between [0,1]!".format(q)

    return Entropy([q, 1-q])


def Boolean_Entropy_counts(p, n):
    """
    Finds the entropy for a Boolean random variable.

    INPUT:
    ------
           p (int or float) : Number or relative fraction of positive instances
           n (int or float) : Number or relative fraction of negative instances

    OUTPUT:
    -------
            Entropy (float) : Entropy of a throwing a coin with chances
                              of P(H, T) = (q, 1 - q) in bits

                              with q = p / (n + p)

    """
    if n==0 and p==0:
        return 0
    q = p / (n + p)
    return Boolean_Entropy(q)

In [6]:
def Remainder_Entropy(Attr, outcome):

    set_of_distinct_values = set(Attr)

    count_distict_values = len(set_of_distinct_values)
    count_distict_outcomes = len(set(outcome))

    assert count_distict_outcomes <= 2, "{} different outcomes but expected Boolean"


    count_total_positives = len([i for i in outcome if i!=0])
    count_total_negatives = len(outcome) - count_total_positives

    import numpy as np

    Attr_np = np.array(Attr)
    outcome_np = np.array(outcome)

    _sum_ = 0

    for value in set_of_distinct_values:
        _outcome_ = outcome_np[Attr_np==value]
        count_positives = len([i for i in _outcome_ if i!=0])
        count_negatives = len(_outcome_) - count_positives

        _entropy_ = Boolean_Entropy_counts(count_positives, count_negatives)
        _weights_ = (count_positives + count_negatives)
        _weights_ = _weights_ / (count_total_positives + count_total_negatives)

        _sum_ += _weights_ * _entropy_

    return _sum_



def Information_Gain(Attr, outcome):
    count_total_positives = len([i for i in outcome if i!=0])
    count_total_negatives = len(outcome) - count_total_positives

    initial_entropy = Boolean_Entropy_counts(count_total_positives, count_total_negatives)
    remaining_entropy = Remainder_Entropy(Attr, outcome)

    info_gain = initial_entropy - remaining_entropy

    return info_gain

In [7]:
import copy
import math
import random

from statistics import mean, stdev
from collections import defaultdict

In [8]:
def euclidean_distance(X, Y):
    return math.sqrt(sum((x - y)**2 for x, y in zip(X, Y)))


def cross_entropy_loss(X, Y):
    n=len(X)
    return (-1.0/n)*sum(x*math.log(y) + (1-x)*math.log(1-y) for x, y in zip(X, Y))


def rms_error(X, Y):
    return math.sqrt(ms_error(X, Y))


def ms_error(X, Y):
    return mean((x - y)**2 for x, y in zip(X, Y))


def mean_error(X, Y):
    return mean(abs(x - y) for x, y in zip(X, Y))


def manhattan_distance(X, Y):
    return sum(abs(x - y) for x, y in zip(X, Y))


def mean_boolean_error(X, Y):
    return mean(int(x != y) for x, y in zip(X, Y))


def hamming_distance(X, Y):
    return sum(x != y for x, y in zip(X, Y))

In [9]:
def _read_data_set(data_file, skiprows=0, separator=None):
    with open(data_file, "r") as f:
        file = f.read()
        lines = file.splitlines()
        lines = lines[skiprows:]

    data_ = [[] for _ in range(len(lines))]

    for i, line in enumerate(lines):
        splitted_line = line.split(separator)
        float_line = []
        for value in splitted_line:
            try:
                value = float(value)
            except ValueError:
                if value=="":
                    continue
                else:
                    pass
            float_line.append(value)
        if float_line:
            data_[i] = float_line

    for line in data_:
        if not line:
            data_.remove(line)

    return data_

def unique(seq):
    """
    Remove any duplicate elements from any sequence,
    works on hashable elements such as int, float,
    string, and tuple.
    """
    return list(set(seq))


def remove_all(item, seq):
    """Return a copy of seq (or string) with all occurrences of item removed."""
    if isinstance(seq, str):
        return seq.replace(item, '')
    else:
        return [x for x in seq if x != item]


def weighted_sample_with_replacement(n, seq, weights):
    """Pick n samples from seq at random, with replacement, with the
    probability of each element in proportion to its corresponding
    weight."""
    sample = weighted_sampler(seq, weights)

    return [sample() for _ in range(n)]


def weighted_sampler(seq, weights):
    """Return a random-sample function that picks from seq weighted by weights."""
    import bisect

    totals = []
    for w in weights:
        totals.append(w + totals[-1] if totals else w)

    return lambda: seq[bisect.bisect(totals, random.uniform(0, totals[-1]))]


def mode(data):
    import collections
    """Return the most common data item. If there are ties, return any one of them."""
    [(item, count)] = collections.Counter(data).most_common(1)
    return item

# argmin and argmax

identity = lambda x: x

argmin = min
argmax = max


def argmin_random_tie(seq, key=identity):
    """Return a minimum element of seq; break ties at random."""
    return argmin(shuffled(seq), key=key)


def argmax_random_tie(seq, key=identity):
    """Return an element with highest fn(seq[i]) score; break ties at random."""
    return argmax(shuffled(seq), key=key)


def shuffled(iterable):
    """Randomly shuffle a copy of iterable."""
    items = list(iterable)
    random.shuffle(items)
    return items

def check_equal(iterator):
    iterator = iter(iterator)
    try:
        first = next(iterator)
    except StopIteration:
        return True
    return all(first == rest for rest in iterator)

def probability(p):
    """Return true with probability p."""
    return p > random.uniform(0.0, 1.0)

In [10]:
class Data_Set:
    """
    Defining a _general_ data set class for machine learning.

    These are the following fields:

    >> data = Data_set

    data.examples:

           list of examples. Each one is a list contains of attribute values.


    data.attributes:

           list of integers to index into an example, so example[attribute]
           gives a value.


    data.attribute_names:

           list of names for corresponding attributes.


    data.target_attribute:

           The target attribute for the learning algorithm.
           (Default = last attribute)


    data.input_attributes:

           The list of attributes without the target.



    data.values:

           It is a list of lists in which each sublist is the
           set of possible values for the corresponding attribute.
           If initially None, it is computed from the known examples
           by self.setproblem. If not None, bad value raises ValueError.


    data.distance_measure:

           A measure  of  distance  function which takes two examples
           and returns a nonnegative number. It should be a symmetric
           function.
           (Defaults = mean_boolean_error) : can handle any field types.


    data.file_info:

           This should be a tuple that contains:
        (file_address, number of rows to skip, separator)



    data.name:

           This is for naming the data set.



    data.source:

            URL or explanation to the dataset main source


    data.excluded_attributes:

            List of attribute indexes to exclude from data.input_attributes.
            (indexes or names of the attributes)

    Normally, you call the constructor and you're done; then you just
    access fields like d.examples and d.target and d.inputs."""




    def __init__(self, examples=None, attributes=None,  attribute_names=None,
                 target_attribute = -1,  input_attributes=None,  values=None,
                 distance_measure = mean_boolean_error, name='',  source='',
                 excluded_attributes=(), file_info=None):

        """
        Accepts any of DataSet's fields. Examples can also be a
        string or file from which to parse examples using parse_csv.
        Optional parameter: exclude, as documented in .setproblem().

        >>> DataSet(examples='1, 2, 3')
        <DataSet(): 1 examples, 3 attributes>
        """

        self.file_info = file_info
        self.name = name
        self.source = source
        self.values = values
        self.distance = distance_measure
        self.check_values_flag = bool(values)

        # Initialize examples from a list
        if examples is not None:
            self.examples = examples
        elif file_info is None:
            raise ValueError("No Examples! and No Address!")
        else:
            self.examples = _read_data_set(file_info[0], file_info[1], file_info[2])

        # Attributes are the index of examples. can be overwrite
        if self.examples is not None and attributes is None:
            attributes = list(range(len(self.examples[0])))

        self.attributes = attributes

        # Initialize attribute_names from string, list, or to default
        if isinstance(attribute_names, str):
            self.attribute_names = attribute_names.split()
        else:
            self.attribute_names = attribute_names or attributes

        # set the definitions needed for the problem
        self.set_problem(target_attribute, input_attributes=input_attributes,
                         excluded_attributes=excluded_attributes)



    def get_attribute_num(self, attribute):
        if isinstance(attribute, str):
            return self.attribute_names.index(attribute)
        else:
            return attribute




    def set_problem(self, target_attribute, input_attributes=None, excluded_attributes=()):
        """
        By doing this we set the target, inputs and excluded attributes.

        This way, one DataSet can be used multiple ways. inputs, if specified,
        is a list of attributes, or specify exclude as a list of attributes
        to not use in inputs. Attributes can be -n .. n, or an attrname.
        Also computes the list of possible values, if that wasn't done yet."""

        self.target_attribute = self.get_attribute_num(target_attribute)

        exclude = [self.get_attribute_num(excluded) for excluded in excluded_attributes]

        if input_attributes:
            self.input_attributes = remove_all(self.target_attribute, input_attributes)
        else:
            inputs = []
            for a in self.attributes:
                if a != self.target_attribute and a not in exclude:
                    inputs.append(a)
            self.input_attributes = inputs

        if not self.values:
            self.update_values()
        self.sanity_check()


    def sanity_check(self):
        """Sanity check on the fields."""

        assert len(self.attribute_names) == len(self.attributes)
        assert self.target_attribute in self.attributes
        assert self.target_attribute not in self.input_attributes
        assert set(self.input_attributes).issubset(set(self.attributes))
        if self.check_values_flag:
            # only check if values are provided while initializing DataSet
            [self.check_example(example) for example in self.examples]


    def check_example(self, example):
        if self.values:
            for attr in self.attributes:
                if example[attr] not in self.values:
                    raise ValueError("Not recognized value of {} for attribute {} in {}"
                                     .format(example[attr], attr, example))


    def add_example(self, example):
        self.check_example(example)
        self.examples.append(example)


    def update_values(self):
        self.values = list(map(unique, zip(*self.examples)))


    def remove_examples(self, value=""):
        self.examples = [example for example in examples if value not in example]

    def sanitize(self, example):  
        """Copy of the examples with non input_attributes replaced by None"""
        _list_ = []
        for i, attr_i in enumerate(example):
            if i in self.input_attributes:
                _list_.append(attr_i)
            else:
                _list_.append(None)
        return _list_

    def train_test_split(self, test_fraction=0.3, Seed = 99):
        import numpy as np

        examples = self.examples
        atrrs = self.attributes
        atrrs_name = self.attribute_names
        target = self.target_attribute
        input_ = self.input_attributes
        name = self.name

        np.random.seed(Seed)
        _test_index = np.random.choice(list(range(len(examples))), int(test_fraction * len(examples)), replace=False)

        test_examples = [example for i, example in enumerate(examples) if i in _test_index]

        train_examples = [example for example in examples if example not in test_examples]

        Test_data_set = Data_Set(examples=test_examples,
                                 attributes=atrrs,
                                 attribute_names=attr_names,
                                 target_attribute=target,
                                 input_attributes=input_,
                                 name=name + " Test set",)

        Train_data_set = Data_Set(examples=train_examples,
                                 attributes=atrrs,
                                 attribute_names=attr_names,
                                 target_attribute=target,
                                 input_attributes=input_,
                                 name=name + " Train set",)

        return Train_data_set, Test_data_set


    def __repr__(self):
        return '<DataSet({}): with {} examples, and {} attributes>'.format(
            self.name, len(self.examples), len(self.attributes))

In [11]:
class Decision_Branch:
    """
    A branch of a decision tree holds an attribute to test, and a dict
    of branches for each attribute's values.
    """

    def __init__(self, attribute, attribute_name=None, default_child=None, branches=None):
        """Initialize by specifying what attribute this node tests."""

        self.attribute = attribute
        self.attribute_name = attribute_name or attribute
        self.default_child = default_child
        self.branches = branches or {}

    def __call__(self, example):
        """Classify a given example using the attribute and the branches."""
        attribute_val = example[self.attribute]
        if attribute_val in self.branches:
            return self.branches[attribute_val](example)
        else:
            # return default class when attribute is unknown
            return self.default_child(example)

    def add(self, value, subtree):
        """Add a branch.  If self.attribute = value, move to the given subtree."""
        self.branches[value] = subtree

    def display_out(self, indent=0):
        name = self.attribute_name
        print("Test", name)
        for value, subtree in self.branches.items():
            print(" " * indent * 5, name, '=', value, "--->", end=" ")
            subtree.display_out(indent + 1)
        # New line
        print()

    def __repr__(self):
        return ('Decision_Branch({}, {}, {})'
                .format(self.attribute, self.attribute_name, self.branches))

In [12]:
class Decision_Leaf:
    """A simple leaf class for a decision tree that hold a result."""

    def __init__(self, result):
        self.result = result

    def __call__(self, example):
        return self.result

    def display_out(self, indent=0):
        print('RESULT =', self.result)

    def __repr__(self):
        return repr(self.result)

In [13]:
def Decision_Tree_Learner(dataset):
    """
    Learning Algorithm for a Decision Tree
    """

    target, values = dataset.target_attribute, dataset.values

    def decision_tree_learning(examples, attrs, parent_examples=()):
        if not examples:
            return plurality(parent_examples)
        elif same_class_for_all(examples):
            return Decision_Leaf(examples[0][target])
        elif not attrs:
            return plurality(examples)
        else:
            A = choose_important_attribute(attrs, examples)
            tree = Decision_Branch(A, dataset.attribute_names[A], plurality(examples))

            for (vk, exs) in split_by(A, examples):
                subtree = decision_tree_learning(
                    exs, remove_all(A, attrs), examples)
                tree.add(vk, subtree)
            return tree

    def plurality(examples):
        """Return the most occured target value for this set of examples.
        (If binary target this is the majority, otherwise plurality)"""
        most_occured = argmax_random_tie(values[target],
                                    key=lambda v: count_example_same_attr(target, v, examples))
        return Decision_Leaf(most_occured)

    def count_example_same_attr(attr, val, examples):
        """Count the number of examples that have example[attr] = val."""
        return sum(e[attr] == val for e in examples)

    def same_class_for_all(examples):
        """Are all these examples in the same target class?"""
        _class_ = examples[0][target]
        return all(example[target] == _class_ for example in examples)

    def choose_important_attribute(attrs, examples):
        """Choose the attribute with the highest information gain."""
        return argmax_random_tie(attrs,
                                 key=lambda a: information_gain(a, examples))

    def information_gain(attr, examples):
        """Return the expected reduction in entropy from splitting by attr."""
        def _entropy_(examples):
            count = []
            for val in values[target]:
                count.append(count_example_same_attr(target, val, examples))
            return Entropy(count)

        N = len(examples)
        remainder = sum((len(examples_i)/N) * _entropy_(examples_i)
                        for (v, examples_i) in split_by(attr, examples))
        return _entropy_(examples) - remainder

    def split_by(attr, examples):
        """Return a list of (val, examples) pairs for each val of attr."""
        return [(v, [e for e in examples if e[attr] == v])
                for v in values[attr]]

    return decision_tree_learning(dataset.examples, dataset.input_attributes)

In [14]:
def Random_Forest(dataset, n=5, verbose=False):
    """
    An ensemble of Decision Trees trained using bagging and feature bagging.

    bagging: Bootstrap aggregating
    """

    def data_bagging(dataset, m=0):
        """Sample m examples with replacement"""
        n = len(dataset.examples)
        return weighted_sample_with_replacement(m or n, dataset.examples, [1]*n)

    def feature_bagging(dataset, p=0.7):
        """Feature bagging with probability p to retain an attribute"""
        inputs = [i for i in dataset.input_attributes if probability(p)]
        return inputs or dataset.input_attributes

    def predict(example):
        if verbose:
            print([predictor(example) for predictor in predictors])
        return mode(predictor(example) for predictor in predictors)

    predictors = [Decision_Tree_Learner(Data_Set(examples=data_bagging(dataset),
                                                 attributes=dataset.attributes,
                                                 attribute_names=dataset.attribute_names,
                                                 target_attribute=dataset.target_attribute,
                                                 input_attributes=feature_bagging(dataset))) for _ in range(n)]

    return predict


In [15]:
train_data="adult.data"
test_data="adult.test"

From the Data zip file, we know the names of the columns (features) are the following,<br>
age: continuous.<br>
workclass: Private, Self-emp-not-inc, Self-emp-inc, Federal-gov, Local-gov, State-gov, Without-pay, Never-worked.<br>
fnlwgt: continuous.<br>
education: Bachelors, Some-college, 11th, HS-grad, Prof-school, Assoc-acdm, Assoc-voc, 9th, 7th-8th, 12th, Masters, 1st-4th, 10th, Doctorate, 5th-6th, Preschool.<br>
education-num: continuous.<br>
marital-status: Married-From the Data zip file, we know the names of the columns (features) are the following,<br>
age: continuous.<br>
workclass: Private, Self-emp-not-inc, Self-emp-inc, Federal-gov, Local-gov, State-gov, Without-pay, Never-worked.<br>
fnlwgt: continuous.<br>
education: Bachelors, Some-college, 11th, HS-grad, Prof-school, Assoc-acdm, Assoc-voc, 9th, 7th-8th, 12th, Masters, 1st-4th, 10th, Doctorate, 5th-6th, Preschool.<br>
education-num: continuous.<br>
marital-status: Married-civ-spouse, Divorced, Never-married, Separated, Widowed, Married-spouse-absent, Married-AF-spouse.<br>
occupation: Tech-support, Craft-repair, Other-service, Sales, Exec-managerial, Prof-specialty, Handlers-cleaners, Machine-op-inspct, Adm-clerical, Farming-fishing, Transport-moving, Priv-house-serv, Protective-serv, Armed-Forces.<br>
relationship: Wife, Own-child, Husband, Not-in-family, Other-relative, Unmarried.<br>
race: White, Asian-Pac-Islander, Amer-Indian-Eskimo, Other, Black.<br>
sex: Female, Male.<br>
capital-gain: continuous.<br>
capital-loss: continuous.<br>
hours-per-week: continuous.<br>
native-country: United-States, Cambodia, England, Puerto-Rico, Canada, Germany, Outlying-US(Guam-USVI-etc), India, Japan, Greece, South, China, Cuba, Iran, Honduras, Philippines, Italy, Poland, Jamaica, Vietnam, Mexico, Portugal, Ireland, France, Dominican-Republic, Laos, Ecuador, Taiwan, Haiti, Columbia, Hungary, Guatemala, Nicaragua, Scotland, Thailand, Yugoslavia, El-Salvador, Trinadad&Tobago, Peru, Hong, Holand-Netherlands.<br>
Income: >50K, <=50Kciv-spouse, Divorced, Never-married, Separated, Widowed, Married-spouse-absent, Married-AF-spouse.<br>
occupation: Tech-support, Craft-repair, Other-service, Sales, Exec-managerial, Prof-specialty, Handlers-cleaners, Machine-op-inspct, Adm-clerical, Farming-fishing, Transport-moving, Priv-house-serv, Protective-serv, Armed-Forces.<br>
relationship: Wife, Own-child, Husband, Not-in-family, Other-relative, Unmarried.<br>
race: White, Asian-Pac-Islander, Amer-Indian-Eskimo, Other, Black.<br>
sex: Female, Male.<br>
capital-gain: continuous.<br>
capital-loss: continuous.<br>
hours-per-week: continuous.<br>
native-country: United-States, Cambodia, England, Puerto-Rico, Canada, Germany, Outlying-US(Guam-USVI-etc), India, Japan, Greece, South, China, Cuba, Iran, Honduras, Philippines, Italy, Poland, Jamaica, Vietnam, Mexico, Portugal, Ireland, France, Dominican-Republic, Laos, Ecuador, Taiwan, Haiti, Columbia, Hungary, Guatemala, Nicaragua, Scotland, Thailand, Yugoslavia, El-Salvador, Trinadad&Tobago, Peru, Hong, Holand-Netherlands.<br>
Income: >50K, <=50K

In [110]:
attr_names =['age','workclass','fnlwgt','edu','edu_num','martial','occupation','relationship','race','sex',
          'capital-gain','capital-loss','hrs_per_week','native-country','income']

In [17]:
train_dataset = Data_Set(name = "Census data",
                      target_attribute=14,
                      attribute_names=attr_names,
                      file_info=(train_data, None, ","))

In [18]:
test_dataset = Data_Set(name = "Census data",
                      target_attribute=14,
                      attribute_names=attr_names,
                      file_info=(train_data, 1, ","))

In [19]:
train_dataset

<DataSet(Census data): with 32561 examples, and 15 attributes>

In [20]:
test_dataset

<DataSet(Census data): with 32560 examples, and 15 attributes>

In [21]:
tree=Decision_Tree_Learner(train_dataset)

In [22]:
tree.display_out()

Test fnlwgt
 fnlwgt = 262153.0 ---> RESULT =  <=50K
 fnlwgt = 262158.0 ---> RESULT =  <=50K
 fnlwgt = 131088.0 ---> RESULT =  <=50K
 fnlwgt = 131091.0 ---> RESULT =  >50K
 fnlwgt = 393248.0 ---> RESULT =  <=50K
 fnlwgt = 131117.0 ---> RESULT =  <=50K
 fnlwgt = 393264.0 ---> RESULT =  <=50K
 fnlwgt = 262196.0 ---> RESULT =  <=50K
 fnlwgt = 262208.0 ---> RESULT =  <=50K
 fnlwgt = 262233.0 ---> RESULT =  >50K
 fnlwgt = 262241.0 ---> RESULT =  <=50K
 fnlwgt = 262244.0 ---> RESULT =  >50K
 fnlwgt = 262245.0 ---> RESULT =  <=50K
 fnlwgt = 131178.0 ---> RESULT =  <=50K
 fnlwgt = 131180.0 ---> RESULT =  <=50K
 fnlwgt = 262280.0 ---> RESULT =  <=50K
 fnlwgt = 393354.0 ---> RESULT =  >50K
 fnlwgt = 393357.0 ---> RESULT =  <=50K
 fnlwgt = 262285.0 ---> RESULT =  <=50K
 fnlwgt = 393360.0 ---> RESULT =  <=50K
 fnlwgt = 131224.0 ---> RESULT =  <=50K
 fnlwgt = 131230.0 ---> RESULT =  <=50K
 fnlwgt = 393376.0 ---> RESULT =  <=50K
 fnlwgt = 131239.0 ---> RESULT =  >50K
 fnlwgt = 131258.0 ---> RESULT = 

 fnlwgt = 394447.0 ---> Test native-country
      native-country =  Philippines ---> RESULT =  >50K
      native-country =  Haiti ---> RESULT =  <=50K
      native-country =  ? ---> RESULT =  <=50K
      native-country =  Mexico ---> RESULT =  <=50K
      native-country =  Yugoslavia ---> RESULT =  >50K
      native-country =  El-Salvador ---> RESULT =  <=50K
      native-country =  Trinadad&Tobago ---> RESULT =  >50K
      native-country =  Dominican-Republic ---> RESULT =  >50K
      native-country =  England ---> RESULT =  <=50K
      native-country =  Cambodia ---> RESULT =  >50K
      native-country =  Hungary ---> RESULT =  >50K
      native-country =  Ireland ---> RESULT =  >50K
      native-country =  Poland ---> RESULT =  >50K
      native-country =  Outlying-US(Guam-USVI-etc) ---> RESULT =  <=50K
      native-country =  Thailand ---> RESULT =  >50K
      native-country =  Vietnam ---> RESULT =  >50K
      native-country =  Taiwan ---> RESULT =  >50K
      native-country =  Pe

 fnlwgt = 394820.0 ---> RESULT =  <=50K
 fnlwgt = 132680.0 ---> RESULT =  <=50K
 fnlwgt = 132683.0 ---> RESULT =  <=50K
 fnlwgt = 132686.0 ---> Test edu
      edu =  5th-6th ---> RESULT =  >50K
      edu =  Bachelors ---> RESULT =  <=50K
      edu =  7th-8th ---> RESULT =  <=50K
      edu =  Preschool ---> RESULT =  >50K
      edu =  Some-college ---> RESULT =  >50K
      edu =  12th ---> RESULT =  <=50K
      edu =  Assoc-voc ---> RESULT =  >50K
      edu =  Prof-school ---> RESULT =  >50K
      edu =  1st-4th ---> RESULT =  >50K
      edu =  HS-grad ---> Test martial
           martial =  Separated ---> RESULT =  <=50K
           martial =  Divorced ---> RESULT =  <=50K
           martial =  Married-civ-spouse ---> RESULT =  >50K
           martial =  Married-spouse-absent ---> RESULT =  >50K
           martial =  Never-married ---> RESULT =  >50K
           martial =  Widowed ---> RESULT =  <=50K
           martial =  Married-AF-spouse ---> RESULT =  <=50K

      edu =  9th ---> RES

      hrs_per_week = 1.0 ---> RESULT =  <=50K
      hrs_per_week = 2.0 ---> RESULT =  <=50K
      hrs_per_week = 3.0 ---> RESULT =  <=50K
      hrs_per_week = 4.0 ---> RESULT =  <=50K
      hrs_per_week = 5.0 ---> RESULT =  <=50K
      hrs_per_week = 6.0 ---> RESULT =  <=50K
      hrs_per_week = 7.0 ---> RESULT =  <=50K
      hrs_per_week = 8.0 ---> RESULT =  <=50K
      hrs_per_week = 9.0 ---> RESULT =  <=50K
      hrs_per_week = 10.0 ---> RESULT =  <=50K
      hrs_per_week = 11.0 ---> RESULT =  <=50K
      hrs_per_week = 12.0 ---> RESULT =  <=50K
      hrs_per_week = 13.0 ---> RESULT =  <=50K
      hrs_per_week = 14.0 ---> RESULT =  <=50K
      hrs_per_week = 15.0 ---> RESULT =  <=50K
      hrs_per_week = 16.0 ---> RESULT =  <=50K
      hrs_per_week = 17.0 ---> RESULT =  <=50K
      hrs_per_week = 18.0 ---> RESULT =  <=50K
      hrs_per_week = 19.0 ---> RESULT =  <=50K
      hrs_per_week = 20.0 ---> RESULT =  <=50K
      hrs_per_week = 21.0 ---> RESULT =  <=50K
      hrs_per_week = 2

      edu_num = 14.0 ---> RESULT =  >50K
      edu_num = 15.0 ---> RESULT =  <=50K
      edu_num = 16.0 ---> RESULT =  >50K

 fnlwgt = 133929.0 ---> RESULT =  <=50K
 fnlwgt = 133935.0 ---> RESULT =  >50K
 fnlwgt = 133937.0 ---> Test martial
      martial =  Separated ---> RESULT =  <=50K
      martial =  Divorced ---> RESULT =  <=50K
      martial =  Married-civ-spouse ---> RESULT =  >50K
      martial =  Married-spouse-absent ---> RESULT =  <=50K
      martial =  Never-married ---> RESULT =  <=50K
      martial =  Widowed ---> RESULT =  <=50K
      martial =  Married-AF-spouse ---> RESULT =  <=50K

 fnlwgt = 133938.0 ---> RESULT =  >50K
 fnlwgt = 527162.0 ---> RESULT =  <=50K
 fnlwgt = 396099.0 ---> RESULT =  <=50K
 fnlwgt = 133963.0 ---> Test occupation
      occupation =  Other-service ---> RESULT =  <=50K
      occupation =  Craft-repair ---> RESULT =  <=50K
      occupation =  Farming-fishing ---> RESULT =  <=50K
      occupation =  ? ---> RESULT =  <=50K
      occupation =  Adm-c

...

 fnlwgt = 129573.0 ---> Test occupation
      occupation =  Other-service ---> RESULT =  <=50K
      occupation =  Craft-repair ---> RESULT =  <=50K
      occupation =  Farming-fishing ---> RESULT =  <=50K
      occupation =  ? ---> RESULT =  <=50K
      occupation =  Adm-clerical ---> RESULT =  <=50K
      occupation =  Tech-support ---> RESULT =  <=50K
      occupation =  Sales ---> Test hrs_per_week
           hrs_per_week = 1.0 ---> RESULT =  <=50K
           hrs_per_week = 2.0 ---> RESULT =  >50K
           hrs_per_week = 3.0 ---> RESULT =  <=50K
           hrs_per_week = 4.0 ---> RESULT =  <=50K
           hrs_per_week = 5.0 ---> RESULT =  >50K
           hrs_per_week = 6.0 ---> RESULT =  <=50K
           hrs_per_week = 7.0 ---> RESULT =  <=50K
           hrs_per_week = 8.0 ---> RESULT =  <=50K
           hrs_per_week = 9.0 ---> RESULT =  >50K
           hrs_per_week = 10.0 ---> RESULT =  >50K
           hrs_per_week = 11.0 ---> RESULT =  <=50K
           hrs_per_week = 12.0 --->

      occupation =  ? ---> RESULT =  <=50K
      occupation =  Adm-clerical ---> RESULT =  <=50K
      occupation =  Tech-support ---> RESULT =  <=50K
      occupation =  Sales ---> RESULT =  <=50K
      occupation =  Transport-moving ---> RESULT =  <=50K
      occupation =  Armed-Forces ---> RESULT =  <=50K
      occupation =  Priv-house-serv ---> RESULT =  <=50K
      occupation =  Machine-op-inspct ---> RESULT =  <=50K
      occupation =  Exec-managerial ---> RESULT =  <=50K
      occupation =  Handlers-cleaners ---> RESULT =  <=50K
      occupation =  Protective-serv ---> RESULT =  <=50K
      occupation =  Prof-specialty ---> RESULT =  <=50K

 fnlwgt = 129699.0 ---> RESULT =  <=50K
 fnlwgt = 129707.0 ---> Test workclass
      workclass =  Self-emp-not-inc ---> RESULT =  >50K
      workclass =  ? ---> RESULT =  >50K
      workclass =  Never-worked ---> RESULT =  >50K
      workclass =  State-gov ---> RESULT =  >50K
      workclass =  Local-gov ---> RESULT =  >50K
      workclass = 

      age = 77.0 ---> RESULT =  >50K
      age = 78.0 ---> RESULT =  <=50K
      age = 79.0 ---> RESULT =  <=50K
      age = 80.0 ---> RESULT =  >50K
      age = 81.0 ---> RESULT =  >50K
      age = 82.0 ---> RESULT =  >50K
      age = 83.0 ---> RESULT =  >50K
      age = 84.0 ---> RESULT =  >50K
      age = 85.0 ---> RESULT =  >50K
      age = 86.0 ---> RESULT =  <=50K
      age = 87.0 ---> RESULT =  >50K
      age = 88.0 ---> RESULT =  <=50K
      age = 90.0 ---> RESULT =  <=50K

 fnlwgt = 130078.0 ---> RESULT =  <=50K
 fnlwgt = 261192.0 ---> RESULT =  <=50K
 fnlwgt = 130125.0 ---> RESULT =  <=50K
 fnlwgt = 130126.0 ---> RESULT =  >50K
 fnlwgt = 261203.0 ---> RESULT =  <=50K
 fnlwgt = 261207.0 ---> RESULT =  <=50K
 fnlwgt = 392286.0 ---> RESULT =  >50K
 fnlwgt = 130143.0 ---> RESULT =  <=50K
 fnlwgt = 261230.0 ---> RESULT =  <=50K
 fnlwgt = 261232.0 ---> RESULT =  <=50K
 fnlwgt = 261241.0 ---> Test capital-loss
      capital-loss = 0.0 ---> RESULT =  >50K
      capital-loss = 2051.0 

      hrs_per_week = 63.0 ---> RESULT =  <=50K
      hrs_per_week = 64.0 ---> RESULT =  <=50K
      hrs_per_week = 65.0 ---> RESULT =  <=50K
      hrs_per_week = 66.0 ---> RESULT =  <=50K
      hrs_per_week = 67.0 ---> RESULT =  <=50K
      hrs_per_week = 68.0 ---> RESULT =  <=50K
      hrs_per_week = 70.0 ---> RESULT =  <=50K
      hrs_per_week = 72.0 ---> RESULT =  <=50K
      hrs_per_week = 73.0 ---> RESULT =  <=50K
      hrs_per_week = 74.0 ---> RESULT =  <=50K
      hrs_per_week = 75.0 ---> RESULT =  <=50K
      hrs_per_week = 76.0 ---> RESULT =  <=50K
      hrs_per_week = 77.0 ---> RESULT =  <=50K
      hrs_per_week = 78.0 ---> RESULT =  <=50K
      hrs_per_week = 80.0 ---> RESULT =  <=50K
      hrs_per_week = 81.0 ---> RESULT =  <=50K
      hrs_per_week = 82.0 ---> RESULT =  <=50K
      hrs_per_week = 84.0 ---> RESULT =  <=50K
      hrs_per_week = 85.0 ---> RESULT =  <=50K
      hrs_per_week = 86.0 ---> RESULT =  <=50K
      hrs_per_week = 87.0 ---> RESULT =  <=50K
      hrs_per

 fnlwgt = 261979.0 ---> RESULT =  <=50K
 fnlwgt = 130926.0 ---> RESULT =  <=50K
 fnlwgt = 130931.0 ---> RESULT =  <=50K
 fnlwgt = 262024.0 ---> RESULT =  <=50K
 fnlwgt = 130957.0 ---> RESULT =  <=50K
 fnlwgt = 130959.0 ---> RESULT =  <=50K
 fnlwgt = 262038.0 ---> RESULT =  <=50K
 fnlwgt = 262042.0 ---> RESULT =  <=50K
 fnlwgt = 262062.0 ---> RESULT =  <=50K
 fnlwgt = 131002.0 ---> RESULT =  >50K
 fnlwgt = 131033.0 ---> RESULT =  <=50K
 fnlwgt = 262116.0 ---> RESULT =  <=50K
 fnlwgt = 131060.0 ---> RESULT =  <=50K
 fnlwgt = 131068.0 ---> RESULT =  <=50K



In [28]:
def Measure_accuracy(true_values, predictions):
    _sum_ = 0
    for truth, prediction in zip(true_values, predictions):
        if truth==prediction:
            _sum_+=1
    return _sum_/len(predictions)

In [29]:
#Accuracy of Decision Tree
tree_pred = [tree(a[:-1]) for a in test_dataset.examples]
tree_true_Test_values = [example[test_dataset.target_attribute] for example in test_dataset.examples]

Measure_accuracy(tree_true_Test_values, tree_pred)

0.9999692874692875

In [23]:
#Random Forest
RF_class=Random_Forest(train_dataset,n=5)

In [25]:
#Accurary of Random Forest
rf_pred = [RF_class(a[:-1]) for a in test_dataset.examples]
true_Test_values = [example[test_dataset.target_attribute] for example in test_dataset.examples]

Measure_accuracy(true_Test_values, rf_pred)

0.9476351351351351

Transforming the data

In [107]:
from sklearn.preprocessing import OneHotEncoder, LabelEncoder
from sklearn.preprocessing import StandardScaler

In [108]:
train_data=pd.read_csv("adult.data", header=None)
test_data=pd.read_csv("adult.test", header=None,skiprows=1)

In [111]:
train_data.columns=attr_names
test_data.columns=attr_names

In [112]:
#Check if there is any null vallues
train_data.isnull().sum()
#No null values for train data

age               0
workclass         0
fnlwgt            0
edu               0
edu_num           0
martial           0
occupation        0
relationship      0
race              0
sex               0
capital-gain      0
capital-loss      0
hrs_per_week      0
native-country    0
income            0
dtype: int64

In [113]:
#Check if there is any null vallues
test_data.isnull().sum()
#No null values for test data

age               0
workclass         0
fnlwgt            0
edu               0
edu_num           0
martial           0
occupation        0
relationship      0
race              0
sex               0
capital-gain      0
capital-loss      0
hrs_per_week      0
native-country    0
income            0
dtype: int64

In [114]:
#We first drop the feature of edu first because it is closely related to edu_num
train_data=train_data.drop('edu',axis=1)
test_data=test_data.drop('edu',axis=1)

In [115]:
train_data

age          workclass  fnlwgt  edu_num              martial  \
0       39          State-gov   77516       13        Never-married   
1       50   Self-emp-not-inc   83311       13   Married-civ-spouse   
2       38            Private  215646        9             Divorced   
3       53            Private  234721        7   Married-civ-spouse   
4       28            Private  338409       13   Married-civ-spouse   
...    ...                ...     ...      ...                  ...   
32556   27            Private  257302       12   Married-civ-spouse   
32557   40            Private  154374        9   Married-civ-spouse   
32558   58            Private  151910        9              Widowed   
32559   22            Private  201490        9        Never-married   
32560   52       Self-emp-inc  287927        9   Married-civ-spouse   

               occupation    relationship    race      sex  capital-gain  \
0            Adm-clerical   Not-in-family   White     Male          2174   
1         Exec-managerial         Husband   White     Male             0   
2       Handlers-cleaners   Not-in-family   White     Male             0   
3       Handlers-cleaners         Husband   Black     Male             0   
4          Prof-specialty            Wife   Black   Female             0   
...                   ...             ...     ...      ...           ...   
32556        Tech-support            Wife   White   Female             0   
32557   Machine-op-inspct         Husband   White     Male             0   
32558        Adm-clerical       Unmarried   White   Female             0   
32559        Adm-clerical       Own-child   White     Male             0   
32560     Exec-managerial            Wife   White   Female         15024   

       capital-loss  hrs_per_week  native-country  income  
0                 0            40   United-States   <=50K  
1                 0            13   United-States   <=50K  
2                 0            40   United-States   <=50K  
3                 0            40   United-States   <=50K  
4                 0            40            Cuba   <=50K  
...             ...           ...             ...     ...  
32556             0            38   United-States   <=50K  
32557             0            40   United-States    >50K  
32558             0            40   United-States   <=50K  
32559             0            20   United-States   <=50K  
32560             0            40   United-States    >50K  

[32561 rows x 14 columns]

In [159]:
train_data_dummies = pd.get_dummies(train_data, columns = ["workclass","martial","occupation","relationship","race","sex","native-country","income"
                                                       ] , prefix_sep = "_",drop_first = True)
test_data_dummies = pd.get_dummies(test_data, columns = ["workclass","martial","occupation","relationship","race","sex","native-country","income"
                                                       ] , prefix_sep = "_",drop_first = True)

In [160]:
#Check the dimension
train_data_dummies.shape,test_data_dummies.shape

((32561, 86), (16281, 85))

The dimension between training and testing data are different, we are going to find out whihc column in testing data is missing

In [120]:
train_data_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32561 entries, 0 to 32560
Data columns (total 86 columns):
 #   Column                                      Non-Null Count  Dtype
---  ------                                      --------------  -----
 0   age                                         32561 non-null  int64
 1   fnlwgt                                      32561 non-null  int64
 2   edu_num                                     32561 non-null  int64
 3   capital-gain                                32561 non-null  int64
 4   capital-loss                                32561 non-null  int64
 5   hrs_per_week                                32561 non-null  int64
 6   workclass_ Federal-gov                      32561 non-null  uint8
 7   workclass_ Local-gov                        32561 non-null  uint8
 8   workclass_ Never-worked                     32561 non-null  uint8
 9   workclass_ Private                          32561 non-null  uint8
 10  workclass_ Self-emp-inc           

In [153]:
test_data_dummies.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16281 entries, 0 to 16280
Data columns (total 85 columns):
 #   Column                                      Non-Null Count  Dtype
---  ------                                      --------------  -----
 0   age                                         16281 non-null  int64
 1   fnlwgt                                      16281 non-null  int64
 2   edu_num                                     16281 non-null  int64
 3   capital-gain                                16281 non-null  int64
 4   capital-loss                                16281 non-null  int64
 5   hrs_per_week                                16281 non-null  int64
 6   workclass_ Federal-gov                      16281 non-null  uint8
 7   workclass_ Local-gov                        16281 non-null  uint8
 8   workclass_ Never-worked                     16281 non-null  uint8
 9   workclass_ Private                          16281 non-null  uint8
 10  workclass_ Self-emp-inc           

"native-country_ Holand-Netherlands" is missing in the testing data. <br>
So, we are going to insert a new column in the column number 58 with all 0 in the test dataset

In [161]:
#Insert a new column "native-country_ Holand-Netherlands" in test_data_dummies
test_data_dummies.insert(58,'native-country_ Holand-Netherlands',0,True)

In [164]:
#Check the dimension
test_data_dummies.shape,train_data_dummies.shape

((16281, 86), (32561, 86))

In [211]:
#Check that specific column
test_data_dummies['native-country_ Holand-Netherlands'].value_counts()
#All 0s

0    16281
Name: native-country_ Holand-Netherlands, dtype: int64

Now, we have the same number of columns in training and testing dataset

In [12]:
#Label Encoder
#le=LabelEncoder()
#train_data_2 = train_data.apply(le.fit_transform)
#test_data_2 = test_data.apply(le.fit_transform)

In [124]:
train_data_dummies

age  fnlwgt  edu_num  capital-gain  capital-loss  hrs_per_week  \
0       39   77516       13          2174             0            40   
1       50   83311       13             0             0            13   
2       38  215646        9             0             0            40   
3       53  234721        7             0             0            40   
4       28  338409       13             0             0            40   
...    ...     ...      ...           ...           ...           ...   
32556   27  257302       12             0             0            38   
32557   40  154374        9             0             0            40   
32558   58  151910        9             0             0            40   
32559   22  201490        9             0             0            20   
32560   52  287927        9         15024             0            40   

       workclass_ Federal-gov  workclass_ Local-gov  workclass_ Never-worked  \
0                           0                     0                        0   
1                           0                     0                        0   
2                           0                     0                        0   
3                           0                     0                        0   
4                           0                     0                        0   
...                       ...                   ...                      ...   
32556                       0                     0                        0   
32557                       0                     0                        0   
32558                       0                     0                        0   
32559                       0                     0                        0   
32560                       0                     0                        0   

       workclass_ Private  ...  native-country_ Puerto-Rico  \
0                       0  ...                            0   
1                       0  ...                            0   
2                       1  ...                            0   
3                       1  ...                            0   
4                       1  ...                            0   
...                   ...  ...                          ...   
32556                   1  ...                            0   
32557                   1  ...                            0   
32558                   1  ...                            0   
32559                   1  ...                            0   
32560                   0  ...                            0   

       native-country_ Scotland  native-country_ South  \
0                             0                      0   
1                             0                      0   
2                             0                      0   
3                             0                      0   
4                             0                      0   
...                         ...                    ...   
32556                         0                      0   
32557                         0                      0   
32558                         0                      0   
32559                         0                      0   
32560                         0                      0   

       native-country_ Taiwan  native-country_ Thailand  \
0                           0                         0   
1                           0                         0   
2                           0                         0   
3                           0                         0   
4                           0                         0   
...                       ...                       ...   
32556                       0                         0   
32557                       0                         0   
32558                       0                         0   
32559                       0                         0   
32560                       0                         0   

      

In [166]:
#Split the data into training and testing
X_train=train_data_dummies.drop('income_ >50K',axis=1)
y_train=train_data_dummies['income_ >50K']
X_test=test_data_dummies.drop('income_ >50K.',axis=1)
y_test=test_data_dummies['income_ >50K.']

In [167]:
#Check the dimension of X_train, y_train, X_test and y_test
X_train.shape, y_train.shape, X_test.shape, y_test.shape

((32561, 85), (32561,), (16281, 85), (16281,))

In [141]:
X_train

age  fnlwgt  edu_num  capital-gain  capital-loss  hrs_per_week  \
0       39   77516       13          2174             0            40   
1       50   83311       13             0             0            13   
2       38  215646        9             0             0            40   
3       53  234721        7             0             0            40   
4       28  338409       13             0             0            40   
...    ...     ...      ...           ...           ...           ...   
32556   27  257302       12             0             0            38   
32557   40  154374        9             0             0            40   
32558   58  151910        9             0             0            40   
32559   22  201490        9             0             0            20   
32560   52  287927        9         15024             0            40   

       workclass_ Federal-gov  workclass_ Local-gov  workclass_ Never-worked  \
0                           0                     0                        0   
1                           0                     0                        0   
2                           0                     0                        0   
3                           0                     0                        0   
4                           0                     0                        0   
...                       ...                   ...                      ...   
32556                       0                     0                        0   
32557                       0                     0                        0   
32558                       0                     0                        0   
32559                       0                     0                        0   
32560                       0                     0                        0   

       workclass_ Private  ...  native-country_ Portugal  \
0                       0  ...                         0   
1                       0  ...                         0   
2                       1  ...                         0   
3                       1  ...                         0   
4                       1  ...                         0   
...                   ...  ...                       ...   
32556                   1  ...                         0   
32557                   1  ...                         0   
32558                   1  ...                         0   
32559                   1  ...                         0   
32560                   0  ...                         0   

       native-country_ Puerto-Rico  native-country_ Scotland  \
0                                0                         0   
1                                0                         0   
2                                0                         0   
3                                0                         0   
4                                0                         0   
...                            ...                       ...   
32556                            0                         0   
32557                            0                         0   
32558                            0                         0   
32559                            0                         0   
32560                            0                         0   

       native-country_ South  native-country_ Taiwan  \
0                          0                       0   
1                          0                       0   
2                          0                       0   
3                          0                       0   
4                          0                       0   
...                      ...                     ...   
32556                      0                       0   
32557                      0                       0   
32558                      0                       0   
32559                      0                       0   
32560                      0                       0   

      

In [205]:
y_train

0        0
1        0
2        0
3        0
4        0
        ..
32556    0
32557    1
32558    0
32559    0
32560    1
Name: income_ >50K, Length: 32561, dtype: uint8

Since we have changed the categorial data into binary 0,1 columns,<br>
we scaled the following features in both training and testing dataset, <br>
age, fnlwgt, edu_num, capital-game, capital-loss, and hrs_per_week

In [182]:
# I reuse the code of Z-scaling from Abtin's notebook
def scale_feature(_feature_):
    _f_ = np.array(_feature_)
    zero_f_ = _f_ - np.average(_f_)
    std = np.std(_f_)
    return zero_f_/std

In [198]:
#Scale for the X_train
X_train_stand=X_train
X_train_stand["age"]=scale_feature(X_train["age"])
X_train_stand["fnlwgt"]=scale_feature(X_train["fnlwgt"])
X_train_stand["edu_num"]=scale_feature(X_train["edu_num"])
X_train_stand["capital-gain"]=scale_feature(X_train["capital-gain"])
X_train_stand["capital-loss"]=scale_feature(X_train["capital-loss"])
X_train_stand["hrs_per_week"]=scale_feature(X_train["hrs_per_week"])

In [199]:
#Scale for the X_test
X_test_stand=X_test
X_test_stand["age"]=scale_feature(X_test["age"])
X_test_stand["fnlwgt"]=scale_feature(X_test["fnlwgt"])                              
X_test_stand["edu_num"]=scale_feature(X_test["edu_num"])
X_test_stand["capital-gain"]=scale_feature(X_test["capital-gain"])
X_test_stand["capital-loss"]=scale_feature(X_test["capital-loss"])
X_test_stand["hrs_per_week"]=scale_feature(X_test["hrs_per_week"])

In [200]:
X_test_stand

age    fnlwgt   edu_num  capital-gain  capital-loss  hrs_per_week  \
0     -0.994129  0.353474 -1.196864     -0.142662     -0.218062     -0.031432   
1     -0.055417 -0.942391 -0.417886     -0.142662     -0.218062      0.769918   
2     -0.777503  1.395450  0.750582     -0.142662     -0.218062     -0.031432   
3      0.377835 -0.275397 -0.028397      0.871091     -0.218062     -0.031432   
4     -1.499590 -0.812954 -0.028397     -0.142662     -0.218062     -0.832781   
...         ...       ...       ...           ...           ...           ...   
16276  0.016791  0.245794  1.140071     -0.142662     -0.218062     -0.351972   
16277  1.822007  1.248371 -0.417886     -0.142662     -0.218062     -0.031432   
16278 -0.055417  1.755221  1.140071     -0.142662     -0.218062      0.769918   
16279  0.377835 -0.998420  1.140071      0.576644     -0.218062     -0.031432   
16280 -0.272043 -0.068939  1.140071     -0.142662     -0.218062      1.571267   

       workclass_ Federal-gov  workclass_ Local-gov  workclass_ Never-worked  \
0                           0                     0                        0   
1                           0                     0                        0   
2                           0                     1                        0   
3                           0                     0                        0   
4                           0                     0                        0   
...                       ...                   ...                      ...   
16276                       0                     0                        0   
16277                       0                     0                        0   
16278                       0                     0                        0   
16279                       0                     0                        0   
16280                       0                     0                        0   

       workclass_ Private  ...  native-country_ Portugal  \
0                       1  ...                         0   
1                       1  ...                         0   
2                       0  ...                         0   
3                       1  ...                         0   
4                       0  ...                         0   
...                   ...  ...                       ...   
16276                   1  ...                         0   
16277                   0  ...                         0   
16278                   1  ...                         0   
16279                   1  ...                         0   
16280                   0  ...                         0   

       native-country_ Puerto-Rico  native-country_ Scotland  \
0                                0                         0   
1                                0                         0   
2                                0                         0   
3                                0                         0   
4                                0                         0   
...                            ...                       ...   
16276                            0                         0   
16277                            0                         0   
16278                            0                         0   
16279                            0                         0   
16280                            0                         0   

       native-country_ South  native-country_ Taiwan  \
0                          0                       0   
1                          0                       0   
2                          0                       0   
3                          0                       0   
4                          0                       0   
...                      ...                     ...   
16276                      0                       0   
16277                      0                       0   
16278                      0                       0   
16279                      0

In [201]:
#Check the dimension of X_train_stand and X_test_stand
X_train_stand.shape, X_test_stand.shape

((32561, 85), (16281, 85))

In [184]:
#from sklearn.preprocessing import StandardScaler
#sc = StandardScaler(with_mean=False)
#X_train_final = sc.fit_transform(X_train)
#X_test_final = sc.fit_transform(X_test)

In [185]:
#X_test_final.shape, X_test_final.shape

((16281, 85), (16281, 85))

3. SVM

In [186]:
from sklearn import svm
#SVM model set Radial as kernel
svm_clf=svm.SVC(kernel="rbf")

In [202]:
svm_clf.fit(X_train_stand, y_train)

SVC(C=1.0, break_ties=False, cache_size=200, class_weight=None, coef0=0.0,
    decision_function_shape='ovr', degree=3, gamma='scale', kernel='rbf',
    max_iter=-1, probability=False, random_state=None, shrinking=True,
    tol=0.001, verbose=False)

In [203]:
y_pred_svm=svm_clf.predict(X_test_stand)
print("The accuracy of the predictions on the test set is =", accuracy_score(y_test, y_pred_svm))

The accuracy of the predictions on the test set is = 0.8588538787543762


In [204]:
print(classification_report(y_test,y_pred_svm))

              precision    recall  f1-score   support

           0       0.88      0.94      0.91     12435
           1       0.76      0.59      0.67      3846

    accuracy                           0.86     16281
   macro avg       0.82      0.77      0.79     16281
weighted avg       0.85      0.86      0.85     16281



SVM has the accuracy of 0.85 while random forest has the accurarcy of 0.947